In [2]:
import numpy as np
import tensorflow as tf
import librosa
import os
import itertools
from jupyterplot import ProgressPlot


In [3]:
# Hack to get it to work with RTX 2000 cards
gpus = tf.config.experimental.list_physical_devices('GPU')
for gpu in gpus:
  tf.config.experimental.set_memory_growth(gpu, True)

2021-11-20 10:02:24.803613: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2021-11-20 10:02:24.845577: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2021-11-20 10:02:24.846024: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero


In [32]:
# Load a file
dataset_dir = './Baggins_Music/'
music_filenames = os.listdir(dataset_dir)

In [33]:
song_np, sr = librosa.load(dataset_dir+music_filenames[0], mono=False)
song_np = np.transpose(song_np)
y.shape

/home/bij/anaconda3/envs/MusicAnalyzer/lib/python3.8/site-packages/librosa/core/audio.py:165: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn("PySoundFile failed. Trying audioread instead.")


In [34]:
# Papers and resources
# WaveNet paper https://arxiv.org/pdf/1609.03499.pdf
# WaveNet AutoEncoder paper (instrument decomp): https://arxiv.org/pdf/1704.01279.pdf
# NSynth: https://magenta.tensorflow.org/nsynth
# WaveNet implementation: https://github.com/ibab/tensorflow-wavenet

In [76]:
# Define the audio autoencoder 
class AudioAutoEncoder(tf.keras.Model):

    def __init__(self, input_len=1024):
        super(AudioAutoEncoder, self).__init__()
        self.input_len = input_len

        # A loss function
        self.mse = tf.keras.losses.MeanSquaredError()
        # An optimizer
        self.optim = tf.keras.optimizers.SGD(learning_rate=0.1, momentum=0.0, nesterov=False, name='SGD')

        # Setup encoder layers
        self.conv1 = tf.keras.layers.Conv1D(filters=32, kernel_size=16, strides=1, dilation_rate=10, activation='relu')
        self.conv2 = tf.keras.layers.Conv1D(filters=32, kernel_size=16, strides=1, dilation_rate=10, activation='relu')
        self.conv3 = tf.keras.layers.Conv1D(filters=32, kernel_size=16, strides=1, dilation_rate=10, activation='relu')
        self.conv4 = tf.keras.layers.Conv1D(filters=32, kernel_size=16, strides=1, dilation_rate=10, activation='relu')
        self.conv5 = tf.keras.layers.Conv1D(filters=32, kernel_size=16, strides=1, dilation_rate=10, activation='relu')
        self.flatten = tf.keras.layers.Flatten()
        self.fc1 = tf.keras.layers.Dense(units=256, activation='relu')
        self.fc2 = tf.keras.layers.Dense(units=128, activation='relu')
        
        # Setup decoder layers
        # Transpose Convolution: https://www.tensorflow.org/api_docs/python/tf/keras/layers/Conv1DTranspose
        self.conv_tp1 = tf.keras.layers.Conv1DTranspose(filters=32, kernel_size=16, strides=2, padding='same', dilation_rate=2, activation='relu')
        self.conv_tp2 = tf.keras.layers.Conv1DTranspose(filters=32, kernel_size=16, strides=2, padding='same', dilation_rate=2, activation='relu')
        self.conv_tp3 = tf.keras.layers.Conv1DTranspose(filters= 2, kernel_size=16, strides=2, padding='same', dilation_rate=2, activation='relu')

    def encoder(self, x):
        x = self.conv1(x)
        x = self.conv2(x)
        x = self.conv3(x)
        x = self.conv4(x)
        x = self.conv5(x)
        # Flatten the layer
        x = self.flatten(x)
        x = self.fc1(x)
        x = self.fc2(x)
        return x
    
    def decoder(self, z):
        z = self.conv_tp1(z)
        z = self.conv_tp2(z)
        z = self.conv_tp3(z)
        #z = self.conv_tp4(z)
        #z = self.conv_tp5(z)
        return z
    
    def calc_loss(self, x_hat, x):
        loss = self.mse(x, x_hat)
        return loss
        
    def call(self, inputs):
        z = self.encoder(inputs)
        z = tf.expand_dims(z, axis=-1)
        x_hat = self.decoder(z)
        
        return x_hat

    

In [92]:
auto_encoder = AudioAutoEncoder()
y = np.random.rand(1, 1024, 2)
print(y.shape)
print(auto_encoder(y).shape)

(1, 1024, 2)
(1, 1024, 2)


In [23]:
conv_tp = tf.keras.layers.Conv1DTranspose(filters=32, kernel_size=16, strides=2, padding='same', dilation_rate=2, activation='relu')
conv_tp(np.zeros((1, 100, 2))).shape

In [42]:
# Prep the dataset
ds_num_samples = int(len(song_np)/auto_encoder.input_len)
song_ds = song_np[0:auto_encoder.input_len*ds_num_samples]
song_ds = np.reshape(song_ds, (ds_num_samples, -1, 2))
song_ds.shape

(67009, 1024, 2)

In [44]:
song_ds[1].shape

(1024, 2)

In [93]:
# Create the dataset

print(ds_num_samples)
batch_size = 256

# For plotting loss
pp = ProgressPlot(plots_names=['Recon Loss'],
                 line_names=['Training Loss'])

# Train the autoencoder
for step in itertools.count():
    # Get the batch
    batch_idxs = np.random.randint(0, ds_num_samples, size=batch_size)
    x = song_ds[batch_idxs]

    # Put batch through model
    
    with tf.GradientTape() as t:
        x_hat = auto_encoder(x)
    
        # Get Loss
        loss_recon = auto_encoder.calc_loss(x_hat, x)
        pp.update(float(loss_recon.numpy()))
        #print('Step {0:8d}\tLoss: {1:3.4f}'.format(step, loss_recon.numpy()))
        grads = t.gradient(loss_recon, auto_encoder.variables)
        
    # Backprop grads
    auto_encoder.optim.apply_gradients(zip(grads, auto_encoder.variables))
    
    
    

67009


<IPython.core.display.Javascript object>

<class 'numpy.float32'>
Step        0	Loss: 0.0240
<class 'numpy.float32'>
Step        1	Loss: 0.0235
<class 'numpy.float32'>
Step        2	Loss: 0.0228
<class 'numpy.float32'>
Step        3	Loss: 0.0237
<class 'numpy.float32'>
Step        4	Loss: 0.0257
<class 'numpy.float32'>
Step        5	Loss: 0.0266
<class 'numpy.float32'>
Step        6	Loss: 0.0258
<class 'numpy.float32'>
Step        7	Loss: 0.0303
<class 'numpy.float32'>
Step        8	Loss: 0.0258
<class 'numpy.float32'>
Step        9	Loss: 0.0256
<class 'numpy.float32'>
Step       10	Loss: 0.0237
<class 'numpy.float32'>
Step       11	Loss: 0.0246
<class 'numpy.float32'>
Step       12	Loss: 0.0261
<class 'numpy.float32'>
Step       13	Loss: 0.0249
<class 'numpy.float32'>
Step       14	Loss: 0.0244
<class 'numpy.float32'>
Step       15	Loss: 0.0245
<class 'numpy.float32'>
Step       16	Loss: 0.0257
<class 'numpy.float32'>
Step       17	Loss: 0.0227
<class 'numpy.float32'>
Step       18	Loss: 0.0266
<class 'numpy.float32'>
Step   

Step      161	Loss: 0.0259
<class 'numpy.float32'>
Step      162	Loss: 0.0283
<class 'numpy.float32'>
Step      163	Loss: 0.0239
<class 'numpy.float32'>
Step      164	Loss: 0.0257
<class 'numpy.float32'>
Step      165	Loss: 0.0271
<class 'numpy.float32'>
Step      166	Loss: 0.0249
<class 'numpy.float32'>
Step      167	Loss: 0.0258
<class 'numpy.float32'>
Step      168	Loss: 0.0271
<class 'numpy.float32'>
Step      169	Loss: 0.0261
<class 'numpy.float32'>
Step      170	Loss: 0.0266
<class 'numpy.float32'>
Step      171	Loss: 0.0240
<class 'numpy.float32'>
Step      172	Loss: 0.0235
<class 'numpy.float32'>
Step      173	Loss: 0.0253
<class 'numpy.float32'>
Step      174	Loss: 0.0227
<class 'numpy.float32'>
Step      175	Loss: 0.0236
<class 'numpy.float32'>
Step      176	Loss: 0.0244
<class 'numpy.float32'>
Step      177	Loss: 0.0264
<class 'numpy.float32'>
Step      178	Loss: 0.0270
<class 'numpy.float32'>
Step      179	Loss: 0.0249
<class 'numpy.float32'>
Step      180	Loss: 0.0260
<cla

Step      322	Loss: 0.0249
<class 'numpy.float32'>
Step      323	Loss: 0.0247
<class 'numpy.float32'>
Step      324	Loss: 0.0260
<class 'numpy.float32'>
Step      325	Loss: 0.0263
<class 'numpy.float32'>
Step      326	Loss: 0.0261
<class 'numpy.float32'>
Step      327	Loss: 0.0280
<class 'numpy.float32'>
Step      328	Loss: 0.0252
<class 'numpy.float32'>
Step      329	Loss: 0.0236
<class 'numpy.float32'>
Step      330	Loss: 0.0238
<class 'numpy.float32'>
Step      331	Loss: 0.0229
<class 'numpy.float32'>
Step      332	Loss: 0.0247
<class 'numpy.float32'>
Step      333	Loss: 0.0247
<class 'numpy.float32'>
Step      334	Loss: 0.0253
<class 'numpy.float32'>
Step      335	Loss: 0.0257
<class 'numpy.float32'>
Step      336	Loss: 0.0266
<class 'numpy.float32'>
Step      337	Loss: 0.0259
<class 'numpy.float32'>
Step      338	Loss: 0.0268
<class 'numpy.float32'>
Step      339	Loss: 0.0254
<class 'numpy.float32'>
Step      340	Loss: 0.0251
<class 'numpy.float32'>
Step      341	Loss: 0.0243
<cla

...

Step    49910	Loss: 0.0182
<class 'numpy.float32'>
Step    49911	Loss: 0.0188
<class 'numpy.float32'>
Step    49912	Loss: 0.0196
<class 'numpy.float32'>
Step    49913	Loss: 0.0226
<class 'numpy.float32'>
Step    49914	Loss: 0.0194
<class 'numpy.float32'>
Step    49915	Loss: 0.0204
<class 'numpy.float32'>
Step    49916	Loss: 0.0228
<class 'numpy.float32'>
Step    49917	Loss: 0.0185
<class 'numpy.float32'>
Step    49918	Loss: 0.0179
<class 'numpy.float32'>
Step    49919	Loss: 0.0208
<class 'numpy.float32'>
Step    49920	Loss: 0.0197
<class 'numpy.float32'>
Step    49921	Loss: 0.0219
<class 'numpy.float32'>
Step    49922	Loss: 0.0209
<class 'numpy.float32'>
Step    49923	Loss: 0.0194
<class 'numpy.float32'>
Step    49924	Loss: 0.0186
<class 'numpy.float32'>
Step    49925	Loss: 0.0199
<class 'numpy.float32'>
Step    49926	Loss: 0.0211
<class 'numpy.float32'>
Step    49927	Loss: 0.0192
<class 'numpy.float32'>
Step    49928	Loss: 0.0188
<class 'numpy.float32'>
Step    49929	Loss: 0.0201
<cla

Step    50071	Loss: 0.0197
<class 'numpy.float32'>
Step    50072	Loss: 0.0187
<class 'numpy.float32'>
Step    50073	Loss: 0.0228
<class 'numpy.float32'>
Step    50074	Loss: 0.0203
<class 'numpy.float32'>
Step    50075	Loss: 0.0207
<class 'numpy.float32'>
Step    50076	Loss: 0.0173
<class 'numpy.float32'>
Step    50077	Loss: 0.0201
<class 'numpy.float32'>
Step    50078	Loss: 0.0184
<class 'numpy.float32'>
Step    50079	Loss: 0.0200
<class 'numpy.float32'>
Step    50080	Loss: 0.0204
<class 'numpy.float32'>
Step    50081	Loss: 0.0193
<class 'numpy.float32'>
Step    50082	Loss: 0.0191
<class 'numpy.float32'>
Step    50083	Loss: 0.0193
<class 'numpy.float32'>
Step    50084	Loss: 0.0235
<class 'numpy.float32'>
Step    50085	Loss: 0.0209
<class 'numpy.float32'>
Step    50086	Loss: 0.0211
<class 'numpy.float32'>
Step    50087	Loss: 0.0187
<class 'numpy.float32'>
Step    50088	Loss: 0.0180
<class 'numpy.float32'>
Step    50089	Loss: 0.0209
<class 'numpy.float32'>
Step    50090	Loss: 0.0190
<cla

Step    50232	Loss: 0.0216
<class 'numpy.float32'>
Step    50233	Loss: 0.0223
<class 'numpy.float32'>
Step    50234	Loss: 0.0218
<class 'numpy.float32'>
Step    50235	Loss: 0.0218
<class 'numpy.float32'>
Step    50236	Loss: 0.0217
<class 'numpy.float32'>
Step    50237	Loss: 0.0195
<class 'numpy.float32'>
Step    50238	Loss: 0.0233
<class 'numpy.float32'>
Step    50239	Loss: 0.0210
<class 'numpy.float32'>
Step    50240	Loss: 0.0203
<class 'numpy.float32'>
Step    50241	Loss: 0.0189
<class 'numpy.float32'>
Step    50242	Loss: 0.0201
<class 'numpy.float32'>
Step    50243	Loss: 0.0180
<class 'numpy.float32'>
Step    50244	Loss: 0.0198
<class 'numpy.float32'>
Step    50245	Loss: 0.0195
<class 'numpy.float32'>
Step    50246	Loss: 0.0194
<class 'numpy.float32'>
Step    50247	Loss: 0.0195
<class 'numpy.float32'>
Step    50248	Loss: 0.0201
<class 'numpy.float32'>
Step    50249	Loss: 0.0199
<class 'numpy.float32'>
Step    50250	Loss: 0.0214
<class 'numpy.float32'>
Step    50251	Loss: 0.0202
<cla

Step    50393	Loss: 0.0199
<class 'numpy.float32'>
Step    50394	Loss: 0.0217
<class 'numpy.float32'>
Step    50395	Loss: 0.0212
<class 'numpy.float32'>
Step    50396	Loss: 0.0192
<class 'numpy.float32'>
Step    50397	Loss: 0.0206
<class 'numpy.float32'>
Step    50398	Loss: 0.0207
<class 'numpy.float32'>
Step    50399	Loss: 0.0210
<class 'numpy.float32'>
Step    50400	Loss: 0.0210
<class 'numpy.float32'>
Step    50401	Loss: 0.0187
<class 'numpy.float32'>
Step    50402	Loss: 0.0206
<class 'numpy.float32'>
Step    50403	Loss: 0.0209
<class 'numpy.float32'>
Step    50404	Loss: 0.0210
<class 'numpy.float32'>
Step    50405	Loss: 0.0192
<class 'numpy.float32'>
Step    50406	Loss: 0.0201
<class 'numpy.float32'>
Step    50407	Loss: 0.0191
<class 'numpy.float32'>
Step    50408	Loss: 0.0210
<class 'numpy.float32'>
Step    50409	Loss: 0.0214
<class 'numpy.float32'>
Step    50410	Loss: 0.0199
<class 'numpy.float32'>
Step    50411	Loss: 0.0186
<class 'numpy.float32'>
Step    50412	Loss: 0.0213
<cla

KeyboardInterrupt: 

In [50]:
batch_idxs = np.random.randint(0, ds_num_samples, size=batch_size)
song_ds[batch_idxs].shape

(10, 1024, 2)

In [86]:
pp = ProgressPlot()
for i in range(1000):
    pp.update(np.sin(i / 100))
pp.finalize()

In [95]:
def dilconv_outlen(input_len, dil_rate, kernel_size):
    return input_len - (kernel_size-1)*dil_rate

def calc_num_layers(tgt_output_len, input_len, dil_rate, kernel_size):
    '''
    Calculates how many encoder layers are required to get to the target output length
    from a given input length, given a few conv1d params. 
    '''
    num_layers = (input_len - tgt_output_len)/((kernel_size-1)*dil_rate)
    return num_layers

# Define the audio autoencoder 
class AudioAutoEncoder(tf.keras.Model):

    def __init__(self, input_dur=1, sample_rate=22050):
        '''
        input_dur: duration of input (in seconds)
        sample_rate: sampling frequency of input audio (in hz) 
        '''
        super(AudioAutoEncoder, self).__init__()
        self.input_len = input_dur*sample_rate
        self.sample_rate = sample_rate

        # A loss function
        self.mse = tf.keras.losses.MeanSquaredError()
        # An optimizer
        self.optim = tf.keras.optimizers.SGD(learning_rate=0.1, momentum=0.0, nesterov=False, name='SGD')

        # Calculate how many layers we need for a receptive field to cover the whole sample
        self.dil_rate = 100
        self.z_len = 1024
        kern_size = 16
        self.num_filts = 16
        self.num_enc_lyrs = int(calc_num_layers(self.z_len, self.input_len, self.dil_rate, kern_size))
        
        
        print('Num Layers: ', self.num_enc_lyrs)
        
        # Setup encoder layers
        self.enc_lyrs = []
        for lyr_num in range(self.num_enc_lyrs):
            if(lyr_num+1 >= self.num_enc_lyrs):
                num_filts = 2
            else:
                num_filts = self.num_filts
            self.enc_lyrs += [tf.keras.layers.Conv1D(filters=num_filts, 
                                                     kernel_size=kern_size, 
                                                     strides=1, 
                                                     dilation_rate=self.dil_rate, 
                                                     activation='relu')]
        
        # Setup encoder layers
        self.dec_lyrs = []
        for lyr_num in range(self.num_enc_lyrs):
            if(lyr_num+1 >= self.num_enc_lyrs):
                num_filts = 2
            else:
                num_filts = self.num_filts
            print(num_filts)
            self.dec_lyrs += [tf.keras.layers.Conv1DTranspose(filters=num_filts, 
                                                     kernel_size=kern_size, 
                                                     strides=1, 
                                                     dilation_rate=self.dil_rate, 
                                                     activation='relu')]
        

        
    def encoder(self, x):
        for idx,lyr in enumerate(self.enc_lyrs):
            #print('Layer: ', idx, '\t', x.shape, idx, '/', len(self.enc_lyrs))
            x = lyr(x)
        return x
    
    def decoder(self, x):
        for idx,lyr in enumerate(self.dec_lyrs):
            #print('Layer: ', idx, '\t', x.shape, idx, '/', len(self.dec_lyrs))
            x = lyr(x)
        return x
    
    def calc_loss(self, x_hat, x):
        loss = self.mse(x, x_hat)
        return loss
        
    def call(self, inputs):
        z = self.encoder(inputs)
        #print('Z shape: ', z.shape)
        x_hat = self.decoder(z)
        
        return x_hat


In [96]:
aae = AudioAutoEncoder()

Num Layers:  14
16
16
16
16
16
16
16
16
16
16
16
16
16
2


In [97]:
aae(np.zeros((1, 22050, 2))).shape

Layer:  0 	 (1, 22050, 2) 0 / 14
Layer:  1 	 (1, 20550, 16) 1 / 14
Layer:  2 	 (1, 19050, 16) 2 / 14
Layer:  3 	 (1, 17550, 16) 3 / 14
Layer:  4 	 (1, 16050, 16) 4 / 14
Layer:  5 	 (1, 14550, 16) 5 / 14
Layer:  6 	 (1, 13050, 16) 6 / 14
Layer:  7 	 (1, 11550, 16) 7 / 14
Layer:  8 	 (1, 10050, 16) 8 / 14
Layer:  9 	 (1, 8550, 16) 9 / 14
Layer:  10 	 (1, 7050, 16) 10 / 14
Layer:  11 	 (1, 5550, 16) 11 / 14
Layer:  12 	 (1, 4050, 16) 12 / 14
Layer:  13 	 (1, 2550, 16) 13 / 14
Z shape:  (1, 1050, 2)
Layer:  0 	 (1, 1050, 2) 0 / 14
Layer:  1 	 (1, 2550, 16) 1 / 14
Layer:  2 	 (1, 4050, 16) 2 / 14
Layer:  3 	 (1, 5550, 16) 3 / 14
Layer:  4 	 (1, 7050, 16) 4 / 14
Layer:  5 	 (1, 8550, 16) 5 / 14
Layer:  6 	 (1, 10050, 16) 6 / 14
Layer:  7 	 (1, 11550, 16) 7 / 14
Layer:  8 	 (1, 13050, 16) 8 / 14
Layer:  9 	 (1, 14550, 16) 9 / 14
Layer:  10 	 (1, 16050, 16) 10 / 14
Layer:  11 	 (1, 17550, 16) 11 / 14
Layer:  12 	 (1, 19050, 16) 12 / 14
Layer:  13 	 (1, 20550, 16) 13 / 14


TensorShape([1, 22050, 2])